In [1]:
import numpy as np 
import os
from glob import glob
from PIL import Image 
import json
import threading

import tensorflow as tf  
import keras.backend.tensorflow_backend as K  
from math import *
import cv2

%matplotlib inline
import matplotlib.pyplot as plt 

from tqdm import tqdm

Using TensorFlow backend.


In [2]:
char_dir = 'G:\\my_code\\python\\MTWI2018\\char_std_6885.txt'
train_img_dir = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\image_train\\'
train_txt_dir = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\txt_train\\'
train_img_out_dir = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\image_train_out_v20190616\\'
train_data_txt_out_dir_200 = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\txt_train_out_v20190616\\train_data_200.txt'
train_data_txt_out_dir_1000 = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\txt_train_out_v20190616\\train_data_1000.txt'
train_data_txt_out_dir_2200 = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\txt_train_out_v20190616\\train_data_2200.txt'
test_data_txt_out_dir = 'G:\\my_code\\python\\MTWI2018\\mtwi_2018_train\\txt_train_out_v20190616\\test_data.txt'

In [3]:
def show_img(img_input):
    plt.imshow(img_input)
    plt.axis('on') # 关掉坐标轴为 off
    plt.title('image') # 图像题目
    plt.show()

In [4]:
global char_to_id
global id_to_char
def getCharIdStr(char_input):#根据字符返回ID字符串，不存在的新加到字典中
    global char_to_id
    global id_to_char
    
    #统一半角全角符号
#     if char_input == '’':
#         char_input = '\''
#     elif char_input == '“' or char_input == '”':
#         char_input = '"'
#     elif char_input == '：':
#         char_input = ':'
#     elif char_input == '；':
#         char_input = ';'
#     elif char_input == '，':
#         char_input = ','
#     elif char_input == '？':
#         char_input = '?'
#     elif char_input == '（':
#         char_input = '('
#     elif char_input == '）':
#         char_input = ')'
#     elif char_input == '！':
#         char_input = '!'
#     elif char_input == '—':
#         char_input = '-'
        
    if char_input in char_to_id:
        return str(char_to_id[char_input])
    else:
        with open(char_dir,'a',encoding='utf-8') as f:
            f.writelines(char_input+'\n')
        char_to_id, id_to_char = loadCharDict()
        return str(char_to_id[char_input])
    
def loadCharDict():
    char=''
    global char_to_id
    global id_to_char
    char_to_id = {}
    id_to_char = {}
    with open(char_dir,encoding='utf-8') as f:
          for ch in f.readlines():
                ch = ch.strip('\r\n')
                char=char+ch
    char =char+'^'
    print('nclass:',len(char))
    
    char_to_id = {j:i for i,j in enumerate(char)}
    id_to_char = {i:j for i,j in enumerate(char)}
    return char_to_id, id_to_char

In [5]:
loadCharDict()

nclass: 6886


({' ': 0,
  '，': 1,
  '的': 2,
  '。': 3,
  '一': 4,
  '是': 5,
  '0': 6,
  '不': 7,
  '在': 8,
  '有': 9,
  '、': 10,
  '人': 11,
  '“': 12,
  '”': 13,
  '了': 14,
  '中': 15,
  '国': 16,
  '大': 17,
  '为': 18,
  '1': 5565,
  ':': 20,
  '上': 21,
  '2': 22,
  '这': 23,
  '个': 24,
  '以': 25,
  '年': 26,
  '生': 27,
  '和': 28,
  '我': 29,
  '时': 30,
  '之': 31,
  '也': 32,
  '来': 33,
  '到': 34,
  '要': 35,
  '会': 36,
  '学': 37,
  '对': 38,
  '业': 39,
  '出': 40,
  '行': 41,
  '公': 42,
  '能': 43,
  '他': 44,
  '于': 45,
  '5': 46,
  'e': 47,
  '3': 5745,
  '而': 49,
  '发': 50,
  '地': 51,
  '可': 52,
  '作': 53,
  '就': 54,
  '自': 55,
  '们': 56,
  '后': 57,
  '成': 58,
  '家': 59,
  '日': 60,
  '者': 61,
  '分': 62,
  '多': 63,
  '下': 64,
  '其': 65,
  '用': 66,
  '方': 67,
  '本': 68,
  '得': 69,
  '子': 70,
  '.': 71,
  '高': 72,
  '4': 73,
  '过': 74,
  '经': 75,
  '6': 76,
  '现': 77,
  '说': 78,
  '与': 79,
  '前': 80,
  'o': 81,
  '理': 82,
  '工': 83,
  '所': 84,
  '力': 85,
  't': 86,
  '如': 87,
  '将': 88,
  '军': 89,
  '部': 90,
  ','

In [6]:
def txt_line_converter(txt_file_path):
    lines = []
    with open(txt_file_path,encoding='utf-8') as f:
        for ch in f.readlines():
            #count += 1
            ch = ch.strip('\r\n')
            temp = ch.split(',',8)#字符中有“,”,需提前结束split
            if temp[8]=='###':
                continue
            temp1 = list(map(lambda x:float(x), temp[0:8]))#字符串转float
            if max(temp1[6],temp1[4]) < min(temp1[0],temp1[2]):#如果标注是从右向左的，转换为从左向右
                temp2 = temp1.copy()
                temp1[0] = temp2[4]
                temp1[1] = temp2[5]
                temp1[2] = temp2[6]
                temp1[3] = temp2[7]
                temp1[4] = temp2[0]
                temp1[5] = temp2[1]
                temp1[6] = temp2[2]
                temp1[7] = temp2[3]
            temp1.append(temp[8])
            lines.append(temp1)
    return lines

In [7]:
def dumpRotateImage(img, degree, pt1, pt2, pt3, pt4):
    height, width = img.shape[:2]
    heightNew = int(width * fabs(sin(radians(degree))) + height * fabs(cos(radians(degree))))
    widthNew = int(height * fabs(sin(radians(degree))) + width * fabs(cos(radians(degree))))
    matRotation = cv2.getRotationMatrix2D((width // 2, height // 2), degree, 1)
    matRotation[0, 2] += (widthNew - width) // 2
    matRotation[1, 2] += (heightNew - height) // 2
    imgRotation = cv2.warpAffine(img, matRotation, (widthNew, heightNew), borderValue=(255, 255, 255))
    pt1 = list(pt1)
    pt4 = list(pt4)

    [[pt1[0]], [pt1[1]]] = np.dot(matRotation, np.array([[pt1[0]], [pt1[1]], [1]]))
    [[pt4[0]], [pt4[1]]] = np.dot(matRotation, np.array([[pt4[0]], [pt4[1]], [1]]))
    ydim, xdim = imgRotation.shape[:2]
    margin_scale = 0.1
    max_y = max(max(1, int(pt1[1])), min(ydim - 1, int(pt4[1])))
    max_y = min(max_y, ydim - 1)#防止仿射变换后越界
    min_y = min(max(1, int(pt1[1])), min(ydim - 1, int(pt4[1])))
    min_y = max(min_y,1)#防止仿射变换后越界
    margin = int(margin_scale * (max_y-min_y)+0.5)
    max_y = min(max_y + margin, ydim - 1)
    min_y = max(min_y - margin,1)#留白
    max_x = max(max(1, int(pt1[0])-5), min(xdim - 1, int(pt4[0])+5))
    min_x = min(max(1, int(pt1[0])-5), min(xdim - 1, int(pt4[0])+5))
    imgOut = imgRotation[min_y : max_y, min_x: max_x]
    imgOut = cv2.resize(imgOut, (int((max_x-min_x)*32/(max_y-min_y)), 32))#缩放为32的统一高度
    return imgOut

In [8]:
txt_files = glob(train_txt_dir + '*.*')

In [9]:
out_lines_200 = []
out_lines_1000 = []
out_lines_2200 = []
error_count = 0
for txt_file in tqdm(sorted(txt_files)):
    txt_file_full_name=os.path.basename(txt_file)
    txt_file_prefix,txt_file_ext=os.path.splitext(txt_file_full_name)
    #print(txt_file_full_name)
    #print(txt_file_prefix)
    #print(txt_file_ext)
    img_file = train_img_dir + txt_file_prefix + '.jpg'
    
    temp_img = np.array(Image.open(img_file).convert('RGB'))
    #show_img(temp_img)
    lines = txt_line_converter(txt_file)
    #print(lines)
    
    xDim, yDim = temp_img.shape[1], temp_img.shape[0]
    count = 0
    for index, line in enumerate(lines):
        count += 1
        
        temLabel = ''
        for char_item in line[8]:
            temLabel += getCharIdStr(char_item)
        if temLabel == '':
            continue
        
        pt1 = (max(1, line[0]), max(1, line[1]))
        pt2 = (line[2], line[3])
        pt3 = (min(line[6], xDim - 2), min(yDim - 2, line[7]))
        pt4 = (line[4], line[5])
            
        degree = degrees(atan2(pt3[1] - pt1[1], pt3[0] - pt1[0]))  # 图像倾斜角度
        try:   
            partImg = dumpRotateImage(temp_img, degree, pt1, pt2, pt3, pt4)
            
            if partImg.shape[0]>partImg.shape[1]*2:
                break
            rect_img_name = txt_file_prefix + '_' + str(count) + '.jpg'
            print(rect_img_name)
            #分档，长0-200一档；201-1000一档；1001-2200一档
            if partImg.shape[1] <= 200:
                partImg = cv2.copyMakeBorder(partImg,0,0,0,200-partImg.shape[1], cv2.BORDER_REPLICATE)#宽度统一填充为200
            elif partImg.shape[1] > 200 and partImg.shape[1] <= 1000:
                partImg = cv2.copyMakeBorder(partImg,0,0,0,1000-partImg.shape[1], cv2.BORDER_REPLICATE)#宽度统一填充为1000
            else:
                partImg = cv2.copyMakeBorder(partImg,0,0,0,2200-partImg.shape[1], cv2.BORDER_REPLICATE)#宽度统一填充为2200
            #partImg = cv2.copyMakeBorder(partImg,0,0,0,2200-partImg.shape[1], cv2.BORDER_CONSTANT,value=[0,255,0])#宽度统一填充为2200
            Image.fromarray(partImg).save(train_img_out_dir + rect_img_name)#保存矩形块，文件名_xxx.jpg
        except:
            error_count+=1
            continue
        out_line = rect_img_name + ' '
        for char_item in line[8]:
            out_line += getCharIdStr(char_item) + ' '
            
        #print(out_line)
        #print(line)
        if partImg.shape[1] == 200:
            out_lines_200.append(out_line)
        elif partImg.shape[1] == 1000:
            out_lines_1000.append(out_line)
        else:
            out_lines_2200.append(out_line)            
        #out_lines.append(out_line)
        
print('失败数：'+ str(error_count))

  0%|                                                                                       | 0/10048 [00:00<?, ?it/s]

T1.3BPFFJdXXXXXXXX_!!0-item_pic.jpg_1.jpg
T1.3BPFFJdXXXXXXXX_!!0-item_pic.jpg_2.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_1.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_2.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_3.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_4.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_5.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_6.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_7.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_8.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_9.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_10.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_11.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_12.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_13.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_14.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_15.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_16.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_17.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_18.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_19.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_20.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_21.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_22.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_23.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_24.jpg
T1.AK_XX8hXXbnu_Z1_042512.jpg_25.jpg


  0%|                                                                               | 2/10048 [00:00<19:37,  8.53it/s]

T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_1.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_2.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_3.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_4.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_5.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_6.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_7.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_8.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_9.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_10.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_11.jpg
T1.MlmFvtbXXXXXXXX_!!0-item_pic.jpg_12.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_1.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_2.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_3.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_4.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_5.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_6.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_7.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_8.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_9.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_10.jpg
T1._WBXtXdXXXXXXXX_!!0-item_pic.jpg_11.jpg
T1._WBXtXdXXXXXXXX_!!0-item_p

  0%|                                                                               | 4/10048 [00:00<18:05,  9.25it/s]

...

TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_1.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_2.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_3.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_4.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_5.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_6.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_7.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_8.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_9.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_10.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_11.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_12.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_13.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_14.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_15.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_16.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_17.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_18.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.jpg_19.jpg
TB2zVize3oQMeJjy0FoXXcShVXa_!!870685124.

100%|██████████████████████████████████████████████████████████████████████████▉| 10046/10048 [14:23<00:00, 12.56it/s]

TB2zfaWel0lpuFjSszdXXcdxFXa_!!2848101018.jpg_1.jpg
TB2zfaWel0lpuFjSszdXXcdxFXa_!!2848101018.jpg_2.jpg
TB2zfaWel0lpuFjSszdXXcdxFXa_!!2848101018.jpg_3.jpg
TB2zfaWel0lpuFjSszdXXcdxFXa_!!2848101018.jpg_4.jpg
TB2zfaWel0lpuFjSszdXXcdxFXa_!!2848101018.jpg_5.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_1.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_2.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_3.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_4.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_5.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_6.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_7.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_8.jpg
TB2zqHkXXkkyKJjSszfXXbdiFXa_!!2599593450.jpg_9.jpg


100%|███████████████████████████████████████████████████████████████████████████| 10048/10048 [14:23<00:00, 11.64it/s]


失败数：42


In [10]:
from sklearn.model_selection import train_test_split

X_train_200, X_test, y_train_200, y_test = train_test_split(
    out_lines_200, out_lines_200, test_size=0.2, random_state=42)

In [11]:
with open(train_data_txt_out_dir_200,'w',encoding='utf-8') as f:
    for x in X_train_200:
        f.writelines(x + '\n')

with open(train_data_txt_out_dir_1000,'w',encoding='utf-8') as f:
    for x in out_lines_1000:
        f.writelines(x + '\n')
        
with open(train_data_txt_out_dir_2200,'w',encoding='utf-8') as f:
    for x in out_lines_2200:
        f.writelines(x + '\n')        
        
with open(test_data_txt_out_dir,'w',encoding='utf-8') as f:
    for x in X_test:
        f.writelines(x + '\n')

In [12]:
y_test[77]

'TB1HSKKRpXXXXcgXXXXXXXXXXXX_!!0-item_pic.jpg_23.jpg 6 94 991 6 105 22 '

In [13]:
X_test[77]

'TB1HSKKRpXXXXcgXXXXXXXXXXXX_!!0-item_pic.jpg_23.jpg 6 94 991 6 105 22 '